<a href="https://colab.research.google.com/github/milver/Experiments/blob/main/Sentinel_LULC.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Experimenting with Sentinel Land Use Land Cover classification

In [23]:
import ee
import geemap

## Set Dependencies

In [ ]:
# %pip install leafmap
# %pip install pystac
# %pip install ipyleaflet==0.18.2

In [3]:
# import leafmap
# import ipywidgets
# import folium
# #import leafmap.foliumap as leafmap

## Get Bounding Box
I prefer to use leafmap for it

In [28]:
Map = geemap.Map()
Map.add_basemap("Esri.NatGeoWorldMap")
Map.set_center(-77.5107765197754, 39.01424883668118, 13)
Map

Map(center=[39.01424883668118, -77.5107765197754], controls=(WidgetControl(options=['position', 'transparent_b…

In [ ]:

# region = Map.user_roi
# if region is None:
#     region = ee.Geometry.BBox(-89.7088, 42.9006, -89.0647, 43.2167)

# Map.centerObject(region)


In [ ]:
m = leafmap.Map(center=[39.01424883668118, -77.5107765197754], zoom = 13, google_map="ROADMAP")
#m.split_map(left_layer="TERRAIN", right_layer="OpenTopoMap")
m

In [5]:
bbox1 = [m.west, m.south, m.east, m.north]
print("{}: {}".format(m.center, m.zoom))


[39.01918369029137, -77.51601219177248]: 14.0


## Extracting Sentinel-2
Construct a collection of corresponding Dynamic World and Sentinel-2 for inspection. Filter the DW and S2 collections by region and date.

### Setting up Earth Engine credentials

In [5]:
    ee.Authenticate()
    ee.Initialize(project='ee-my-milver')

### Function to convert bbox to GeoJson bbox

In [7]:
# import json

# def bbox_to_geojson(bbox):
#   """Converts a bounding box to GeoJSON.

#   Args:
#     bbox: A list of four numbers, representing the minimum and maximum
#       longitude and latitude of the bounding box.

#   Returns:
#     A GeoJSON object representing the bounding box.
#   """

#   return {
#     "type": "Feature",
#     "geometry": {
#       "type": "Polygon",
#       "coordinates": [[
#           [bbox[0], bbox[1]],
#           [bbox[2], bbox[1]],
#           [bbox[2], bbox[3]],
#           [bbox[0], bbox[3]],
#           [bbox[0], bbox[1]],
#       ]]
#     },
#     "properties": {
#       "bbox": bbox
#     }
#   }



### Make the conversions to GeoJson and then to ee object
...which is kind of annoying that ee does not take the geojson object directly but likely I'm missing something but this works so far

In [ ]:
# import geemap
# bounds1 = bbox_to_geojson(bbox1)
# eebounds = geemap.geojson_to_ee(bounds1)
# print(eebounds)


### Start the filtering

In [14]:
START = ee.Date('2021-04-02')
END = ee.Date('2024-04-02')  #START.advance(1, 'day')

col_filter = ee.Filter.And(
    ee.Filter.bounds(ee.Geometry.Point(-77.51601219177248, 39.01918369029137)),
    ee.Filter.date(START, END),
)

dw_col = ee.ImageCollection('GOOGLE/DYNAMICWORLD/V1').filter(col_filter)
s2_col = ee.ImageCollection('COPERNICUS/S2_HARMONIZED').filter(col_filter)

# Join corresponding DW and S2 images (by system:index).
dw_s2_col = ee.Join.saveFirst('s2_img').apply(
    dw_col,
    s2_col,
    ee.Filter.equals(leftField='system:index', rightField='system:index'),
)

### Construct a collection of corresponding Dynamic World and  Sentinel-2 for inspection.
Filter the DW and S2 collections by region and date.

In [15]:
# Extract an example DW image and its source S2 image.
dw_image = ee.Image(dw_s2_col.first())
s2_image = ee.Image(dw_image.get('s2_img'))

# Create a visualization that blends DW class label with probability.
# Define list pairs of DW LULC label and color.
CLASS_NAMES = [
    'water',
    'trees',
    'grass',
    'flooded_vegetation',
    'crops',
    'shrub_and_scrub',
    'built',
    'bare',
    'snow_and_ice',
]

VIS_PALETTE = [
    '419bdf',
    '397d49',
    '88b053',
    '7a87c6',
    'e49635',
    'dfc35a',
    'c4281b',
    'a59b8f',
    'b39fe1',
]

# Create an RGB image of the label (most likely class) on [0, 1].
dw_rgb = (
    dw_image.select('label')
    .visualize(min=0, max=8, palette=VIS_PALETTE)
    .divide(255)
)

# Get the most likely class probability.
top1_prob = dw_image.select(CLASS_NAMES).reduce(ee.Reducer.max())

# Create a hillshade of the most likely class probability on [0, 1]
top1_prob_hillshade = ee.Terrain.hillshade(top1_prob.multiply(100)).divide(255)

# Combine the RGB image with the hillshade.
dw_rgb_hillshade = dw_rgb.multiply(top1_prob_hillshade)



In [23]:
#!pip install geemap --upgrade
# import ee

# # Initialize the Earth Engine module.
# ee.Initialize()

# # Assuming s2_image is your ee.Image object
# # Specify the visualization parameters.
# vis_params = {
#     'min': 0,
#     'max': 3000,
#     'bands': ['B4', 'B3', 'B2']
# }

# try:
#     # Get the URL for the image.
#     url = s2_image.getThumbURL(vis_params)
#     print("You can view the image at this URL:", url)
# except Exception as e:
#     print("Failed to create image URL:", e)



Failed to create image URL: Element.get: Parameter 'object' is required.


In [20]:
%pip install -q -U geemap

In [22]:
# Display the Dynamic World visualization with the source Sentinel-2 image.
import geemap
m = geemap.Map()
m.set_center(-77.5107765197754, 39.01424883668118, 12)
m.add_layer(
    s2_image,
    {'min': 0, 'max': 3000, 'bands': ['B4', 'B3', 'B2']},
    'Sentinel-2 L1C',
)
m.add_layer(
    dw_rgb_hillshade,
    {'min': 0, 'max': 0.65},
    'Dynamic World V1 - label hillshade',
)
m.add_legend(keys=CLASS_NAMES, colors=VIS_PALETTE, position="bottomleft")
m

Map(center=[39.01424883668118, -77.5107765197754], controls=(WidgetControl(options=['position', 'transparent_b…

AttributeError: 'NoneType' object has no attribute 'cleanup'

AttributeError: 'NoneType' object has no attribute 'cleanup'

In [13]:
dw_image